In [551]:
!pip install inflection

In [552]:
!pip install ydata_profiling

In [553]:
!pip install pandas_profiling

In [554]:
!pip install pandasql

In [555]:
!pip install python-dateutil

## i. O DESAFIO

*   De posse de um dataset contendo informações sobre diversos modelos de carros com seus respectivos preços de venda, tomou-se a decisão de aplicar um modelo de machine learning capaz de realizar a **previsão** de preço de novas entradas na base de dados.

*   After collecting data from their clients database during the period of 1 year, the company's marketing team is analyzing wheter it would be profitable or not to separate it into distinct groups, in order to distinguish those who represent a larger ammount of the company's earnings.

*   De posse da solução, times de negócio podem simular com maior clareza quais os fatores que mais influenciam no preço de venda, tomando vantagem nos negócios a partir de soluções adotadas a partir de dados (Data Driven)

## ii. QUESTÕES DE NEGÓCIO

*   Ao término da aplicação do modelo, é esperado um relatório contendo respostas e curso de ação para as seguintes perguntas:

    1.  Quais as características(features) que mais influenciam a alteração do preço do veículo ?
    
    2.  Quais as premissas tomadas ao longo do processo de tratamento, análise de dados e feature engineering?

    3.  Qual a performance do modelo aplicado e como expressar-los à times de negócio?

    4.  Como colocar o modelo em produção?
    
    5.  Quais são possíveis rotas para a melhoria contínua do modelo?



# 0.0 IMPORTS, FUNÇÕES E DATA LOAD

## 0.1 Imports

In [556]:
import pandas       as pd
import numpy        as np
import seaborn      as sns
import math
import ipywidgets
import inflection
import warnings
import os

from matplotlib         import pyplot as plt
from collections        import Counter
from ydata_profiling    import ProfileReport
from pandasql           import sqldf
from dateutil           import parser as date_parser

from sklearn.preprocessing      import MinMaxScaler, StandardScaler
from sklearn.dummy              import DummyClassifier
from sklearn.ensemble           import RandomForestRegressor, ExtraTreesClassifier
from sklearn.linear_model       import LogisticRegression
from sklearn.neighbors          import KNeighborsClassifier
from sklearn.model_selection    import train_test_split, StratifiedKFold, KFold
from sklearn.metrics            import log_loss

from imblearn.ensemble          import BalancedRandomForestClassifier
from imblearn.pipeline          import Pipeline
from imblearn.combine           import SMOTEENN
from imblearn.under_sampling    import EditedNearestNeighbours

from IPython.core.display import HTML
from IPython.display      import Image

## 0.2 Funções Auxiliares

In [557]:
warnings.filterwarnings ('ignore')

def jupyter_settings():
    %matplotlib inline
    %pylab inline

    plt.style.use( 'bmh' )
    plt.rcParams['figure.figsize'] = [25, 12]
    plt.rcParams['font.size'] = 24

    display( HTML( '<style>.container { width:90% !important; }</style>') )
    pd.options.display.max_columns = None
    pd.options.display.max_rows = None
    pd.set_option( 'display.expand_frame_repr', False )

    sns.set()

In [558]:
jupyter_settings()

Populating the interactive namespace from numpy and matplotlib


## 0.3 Database load

In [559]:
df0 = pd.read_csv('datasets/car_prices.csv')
df0.sample(5)

year       make           model        trim          body transmission                vin state  condition  odometer  color interior                            seller      mmr  sellingprice                                 saledate
9025    2011  Chevrolet         Equinox         LT1           SUV    automatic  2cnaldec5b6214705    ga       39.0  131158.0   gray    black                   td auto finance   7075.0        7100.0  Thu Dec 18 2014 10:00:00 GMT-0800 (PST)
74779   2012   Infiniti         G Coupe         G37       G Coupe    automatic  jn1cv6ek6cm421457    ca       26.0   35237.0  white    black                nissan infiniti lt  21500.0       20500.0  Tue Jan 13 2015 12:30:00 GMT-0800 (PST)
503828  2013  Chevrolet  Silverado 1500  Work Truck  extended cab    automatic  1gcrcpex6dz368102    nv       29.0   32595.0  black    black                      gm financial  16550.0       15000.0  Fri Jun 05 2015 05:00:00 GMT-0700 (PDT)
428887  2012       Ford            Flex     Limited         Wagon    automatic  2fmgk5dc2cbd00227    fl       42.0  104759.0      —    black  ford motor credit company llc pd  15750.0       14100.0  Thu May 21 2015 02:00:00 GMT-0700 (PDT)
29466   1999     Toyota           Camry          LE         Sedan    automatic  jt2bg22k1x0375266    ga        NaN  283367.0   gray    beige           lewis page auto brokers   1000.0         800.0  Thu Dec 18 2014 10:00:00 GMT-0800 (PST)

In [560]:
#df0 = pd.read_csv('/home/valquiriaam/repos/case_dasa/datasets/car_prices.csv')
#df0.sample(5)

In [561]:
print(f'Number of Rows: {df0.shape[0]}')
print(f'Number of Columns: {df0.shape[1]}')

Number of Rows: 558837
Number of Columns: 16


# 1.0 DESCRIÇÃO DOS DADOS

In [562]:
df1 = df0.copy()

In [563]:
df1.columns

Index(['year', 'make', 'model', 'trim', 'body', 'transmission', 'vin', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'mmr',
       'sellingprice', 'saledate'],
      dtype='object')

In [564]:
cols_old = [ 'year', 'make', 'model', 'trim', 'body', 'transmission', 'vin', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'mmr',
       'sellingprice', 'saledate']
snakecase = lambda x: inflection.underscore(x)
cols_new = list(map(snakecase, cols_old))

df1.columns = cols_new
df1.columns

Index(['year', 'make', 'model', 'trim', 'body', 'transmission', 'vin', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'mmr',
       'sellingprice', 'saledate'],
      dtype='object')

In [565]:
#Reordenando Colunas
cols = ['vin', 'year', 'make', 'model', 'trim', 'body', 'transmission', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'saledate',
       'mmr', 'sellingprice']

df1 = df1[cols]
df1.sample()

vin  year   make            model     trim      body transmission state  condition  odometer  color interior       seller                                 saledate      mmr  sellingprice
529022  3d7mx48c86g224016  2006  Dodge  Ram Pickup 3500  Laramie  quad cab          NaN    pa       31.0  129523.0  white     gray  alans autos  Fri Jun 12 2015 02:00:00 GMT-0700 (PDT)  20600.0       19100.0

## 1.1 Overview Geral

In [566]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 558837 entries, 0 to 558836
Data columns (total 16 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   vin           558833 non-null  object 
 1   year          558837 non-null  int64  
 2   make          548536 non-null  object 
 3   model         548438 non-null  object 
 4   trim          548186 non-null  object 
 5   body          545642 non-null  object 
 6   transmission  493485 non-null  object 
 7   state         558837 non-null  object 
 8   condition     547017 non-null  float64
 9   odometer      558743 non-null  float64
 10  color         558088 non-null  object 
 11  interior      558088 non-null  object 
 12  seller        558837 non-null  object 
 13  saledate      558825 non-null  object 
 14  mmr           558799 non-null  float64
 15  sellingprice  558825 non-null  float64
dtypes: float64(4), int64(1), object(11)
memory usage: 68.2+ MB


In [567]:
df1_profile = ProfileReport(df1, title='Profile Report')
df1_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

*   vin: Código de identificação de veículo

*   year: Ano de Fabricação do Veículo

*   make: Montadora Fabricante do Veículo

*   model: Modelo do Veículo

*   trim: Versão de acabamento do véiculo

*   body: Categoria de carroceria do veículo

*   transmission: Tipo de Transmissão

*   state: Estado onde o veículo foi fabricado

*   condition: Pontuação que expressa a condição do veículo (Valores de 0 a 50)

*   odometer: Medição do Hodômetro indicado pelo veículo(Distância Percorrida)

*   color: Cor do Véiculo

*   interior: Acabamento Interno

*   seller: Vendedor/Revendedora

*   saledate: Data de venda

*   mmr: (Manheim Market Report) - Valor de venda estimada para o veículo, estabelecido pela rede de casas de leilão Manheim, presente em todos os Estados dos EUA.

*   sellingprice: Preço Vendido

## 1.2 Tratamento de Dados Faltantes/Inconsistentes

### 1.2.1 Coluna 'vin' (Reorganização do dataset)

In [568]:
#Coluna vin

df1[df1['vin'] == 'automatic'].sample(5)

vin  year        make  model                    trim         body transmission              state  condition  odometer  color interior seller saledate  mmr  sellingprice
520461  automatic  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  Navitgation        sedan  3vwd17ajxfm315938        NaN       1.0    721     blue   gray     8500  NaN       14100.0
427040  automatic  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  Navitgation        Sedan  3vwd17aj0fm227318        NaN      41.0  14872     gray  black    14300  NaN       13700.0
501455  automatic  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  Navitgation        sedan  3vwd17aj6fm231972        NaN      38.0   9837      red  black    12900  NaN       13500.0
529622  automatic  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  Navitgation        sedan  3vwd17aj5fm225953        NaN      41.0  18561    black  black    13100  NaN       13200.0
444501  automatic  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  Navitgation        Sedan  3vwd17aj5fm297123        NaN       2.0   6388    white  black    10700  NaN       13850.0

In [569]:
df1['body'] = df1.apply(lambda x: 'sedan' if x['vin'] == 'automatic' else
                                             x['body'], axis=1)

df1['transmission'] = df1.apply(lambda x: 'automatic' if x['vin'] == 'automatic' else
                                                         x['transmission'], axis=1)

df1['condition'] = df1.apply(lambda x: x['odometer'] if x['vin'] == 'automatic' else
                                                        x['condition'], axis=1)

df1['odometer'] = df1.apply(lambda x: x['color'] if x['vin'] == 'automatic' else
                                                    x['odometer'], axis=1)

df1['color'] = df1.apply(lambda x: x['interior'] if x['vin'] == 'automatic' else
                                                    x['color'], axis=1)

df1['interior'] = df1.apply(lambda x: x['seller'] if x['vin'] == 'automatic' else
                                                     x['interior'], axis=1)

df1['seller'] = df1.apply(lambda x: '-' if x['vin'] == 'automatic' else
                                           x['seller'], axis=1)

df1['mmr'] = df1.apply(lambda x: x['saledate'] if x['vin'] == 'automatic' else
                                                  x['mmr'], axis=1)

df1['saledate'] =  df1.apply(lambda x: 'Tue Dec 16 2014 12:30:00 GMT-0800 (PST)' if x['vin'] == 'automatic' else
                                                                                    x['saledate'], axis=1)

df1['vin'] =  df1.apply(lambda x: x['state'] if x['vin'] == 'automatic' else
                                                x['vin'], axis=1)

df1['state'] =  df1.apply(lambda x: 'ca' if x['vin'] == x['state'] else
                                            x['state'], axis=1)


In [570]:
df1 = df1.dropna(subset=['vin'])


In [571]:
df1[df1['vin'] == '3vwd17aj4fm201708'].sample()

vin  year        make  model                    trim   body transmission state  condition odometer   color interior seller                                 saledate    mmr  sellingprice
408161  3vwd17aj4fm201708  2015  Volkswagen  Jetta  SE PZEV w/Connectivity  sedan    automatic    ca       46.0     4802  silver     gray      -  Tue Dec 16 2014 12:30:00 GMT-0800 (PST)  16500       13200.0

### 1.2.2 Preenchimento dos dados faltantes nas demais colunas

## Observações e premissas adotadas para cada coluna:

*   vin: A Coluna com o indicador de código de identificação do veículo 'vin', apresentava inconsistência para valores observados como 'automatic' no pandas profiling: Tais entradas foram corrigidas, assumindo transmissão como 'automática' e Estado de produção do veículo como 'ca' (Preenchimento por voto de maioria). Valores faltantes (NaN) tiveram suas linhas removidas.

*   make: Entradas com a coluna 'make' faltante (NaN), também apresentaram dados faltantes para demais características do carro (model, body, trim), sendo descartadas pela impossibilidade de ganho de informação

*   model: Entradas faltantes para 'model' foram observados para modelos que não fazem distinção de modelo/acabamento. Valores 'NaN' foram preenchidos com o nome do modelo, colocados inicialmente na coluna 'trim'.

*   trim: Modelos que não tem distinção de acabamento tiveram valores ausentes preenchidos com '-'

*   body: Modelos sem especificação de carroceria foram preenchidos com valor '-'.

*   transmission: Valores faltantes preenchidos como 'automatic', por voto de maioria absoluta no dataset.

*   condition: Os dados faltantes foram preenchidos com o score equivalente a mediana da base de dados encontradas pelo pandas profiling, que é o valor de 31.

*   odometer: Os dados faltantes foram preenchidos com o valor médio de distância percorrida das entradas presentes no dataset, que é o valor de 68320 milhas.

*   color: Dados Faltantes preenchidos com '-'.

*   interior: Dados faltantes preenchidos com '-'.

*   saledate: Linhas com valores faltantes removidas

*   mmr: Linhas com valores faltantes removidas

*   sellingprice:Linhas com valores faltantes removidas

## NOTA: Por observação no pandas profiling e  preenchimento do dado de cada coluna, não foram observados outliers ou dados anormais nas distribuições de cada coluna.

In [572]:
df1 = df1.dropna(subset=['make'])

In [573]:
df1['model'] = df1.apply(lambda x: x['trim'] if pd.isna(x['model']) else
                                                x['model'], axis=1)

df1['trim'] = df1.apply(lambda x: '-' if pd.isna(x['trim']) else
                                         x['trim'], axis=1)

df1['body'] = df1.apply(lambda x: '-' if pd.isna(x['body']) else
                                         x['body'], axis=1)

df1['transmission'] = df1.apply(lambda x: 'automatic' if pd.isna(x['transmission']) else
                                                         x['transmission'], axis=1)

df1['condition'] = df1.apply(lambda x: 31 if pd.isna(x['condition']) else
                                             x['condition'], axis=1)

df1['odometer'] = df1.apply(lambda x: 68320 if pd.isna(x['odometer']) else
                                               x['odometer'], axis=1)

df1['color'] = df1.apply(lambda x: '-' if pd.isna(x['color']) else
                                          x['color'], axis=1)

df1['interior'] = df1.apply(lambda x: '-' if pd.isna(x['interior']) else
                                          x['interior'], axis=1)

In [574]:
df1.drop

df1 = df1.dropna(subset=['saledate', 'mmr', 'sellingprice'])

In [575]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 548520 entries, 0 to 558836
Data columns (total 16 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   vin           548520 non-null  object 
 1   year          548520 non-null  int64  
 2   make          548520 non-null  object 
 3   model         548520 non-null  object 
 4   trim          548520 non-null  object 
 5   body          548520 non-null  object 
 6   transmission  548520 non-null  object 
 7   state         548520 non-null  object 
 8   condition     548520 non-null  float64
 9   odometer      548520 non-null  object 
 10  color         548520 non-null  object 
 11  interior      548520 non-null  object 
 12  seller        548520 non-null  object 
 13  saledate      548520 non-null  object 
 14  mmr           548520 non-null  object 
 15  sellingprice  548520 non-null  float64
dtypes: float64(2), int64(1), object(13)
memory usage: 71.1+ MB


## 1.3 Tipificação dos Dados e Tratamento dos Valores de Data (Coluna 'saledate')

*   A tipagem das colunas 'condition', 'odometer' e 'mmr' serão alteradas para valores numéricos

*   A coluna 'salesdate' (que contém a data de venda do veículo), será desmembrada de forma a permitir maior precisão nas análises envolvendo datas.

In [576]:
df1['condition'] = df1['condition'].astype(np.int64)

df1['odometer'] = df1['odometer']. astype(np.int64)

df1['mmr'] = df1['mmr']. astype(np.float64)

In [577]:
df1['day_of_week'] = df1['saledate'].apply(lambda x: date_parser.parse(x).strftime('%a'))

#'saledate' conversion to datetime
df1['saledate'] = df1['saledate'].apply(lambda x: date_parser.parse(x).strftime('%Y-%m-%d'))
df1['saledate'] = pd.to_datetime(df1['saledate'])

#year_sold
df1['year_sold'] = df1['saledate'].dt.year.astype(np.int64)

#month_sold
df1['month_sold'] = df1['saledate'].dt.month.astype(np.int64)

#day_sold
df1['day_sold'] = df1['saledate'].dt.day.astype(np.int64)

In [578]:
df1.columns

Index(['vin', 'year', 'make', 'model', 'trim', 'body', 'transmission', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'saledate',
       'mmr', 'sellingprice', 'day_of_week', 'year_sold', 'month_sold',
       'day_sold'],
      dtype='object')

In [579]:
df1.drop(columns=['saledate'], axis=1, inplace=True)

In [580]:
#Reordenando Colunas
cols = ['vin', 'year', 'make', 'model', 'trim', 'body', 'transmission', 'state',
       'condition', 'odometer', 'color', 'interior', 'seller', 'year_sold',
       'month_sold', 'day_sold','day_of_week', 'mmr', 'sellingprice']

df1 = df1[cols]
df1.sample(5)

vin  year     make          model  trim      body transmission state  condition  odometer  color interior                                  seller  year_sold  month_sold  day_sold day_of_week      mmr  sellingprice
348261  2c3cdxct0eh143697  2014    Dodge        Charger   R/T     Sedan    automatic    mo         39     15803  black    black                        chrysler capital       2015           2        25         Wed  23800.0       22200.0
293198  1g2nf52f02c112516  2002  Pontiac       Grand Am   SE1     Sedan    automatic    ga          2    172284  white     gray                            purple heart       2015           2        12         Thu    775.0        1100.0
266218  wbafr9c56cdv58540  2012      BMW       5 Series  550i     Sedan    automatic    ca         49     42969   gray    black  financial services remarketing (lease)       2015           2        12         Thu  37200.0       37000.0
195400  1d7hw42kx7s108248  2007    Dodge         Dakota   SLT  Club Cab    automatic    ma         27     53462   gray     gray         elmwood chrysler dodge jeep ram       2015           2         3         Tue  10700.0       10600.0
277565  2c4rdgcg4cr223875  2012    Dodge  Grand Caravan   SXT   Minivan    automatic    fl         34     63488   gray    black                   the hertz corporation       2015           2        11         Wed  10600.0       11300.0

In [581]:
df1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 548520 entries, 0 to 558836
Data columns (total 19 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   vin           548520 non-null  object 
 1   year          548520 non-null  int64  
 2   make          548520 non-null  object 
 3   model         548520 non-null  object 
 4   trim          548520 non-null  object 
 5   body          548520 non-null  object 
 6   transmission  548520 non-null  object 
 7   state         548520 non-null  object 
 8   condition     548520 non-null  int64  
 9   odometer      548520 non-null  int64  
 10  color         548520 non-null  object 
 11  interior      548520 non-null  object 
 12  seller        548520 non-null  object 
 13  year_sold     548520 non-null  int64  
 14  month_sold    548520 non-null  int64  
 15  day_sold      548520 non-null  int64  
 16  day_of_week   548520 non-null  object 
 17  mmr           548520 non-null  float64
 18  sellingpr

# 2.0 DATA PREPARATION

## 2.1 Hypothesis Creation

In [ ]:
df2 = df1.copy()

### 2.1.1 Hypothesis Mindmap

### 2.1.2 Created Hypothesis

## 2.2 EDA and Feature Engineering

### 2.2.1 Univariative Analysis

In [ ]:
df2_num = df2.select_dtypes(include=['int64', 'float64'])

df2_num.hist(bins=25);

*** Verificar comportamento das distribuições/outliers ***
*** Verificar Comportamento das variáveis categóricas ***

### 2.2.2 Bivariative Analysis

***Validação das Hipóteses/ Feature Engineering/ Mapa de Calor ***

## 2.3 Data Preparation

## 2.4 Feature Selection

# 3.0 MODELING

# 4.0 RESULTS VALIDATION

# 5.0 MODEL IMPLEMENTATION